# OCEL Variant Explorer

In [1]:
import pandas as pd
import pm4py
import pydot

In [2]:
# Cell 2: Load and parse OCEL data
ocel = pm4py.read_ocel("results/mover_OCEL.jsonocel")
df = ocel.relations

# Clean and convert data types
df['ocel:timestamp'] = pd.to_datetime(df['ocel:timestamp'])
df = df[df['ocel:eid'].str.strip() != '']  # Remove empty rows

print("Data loaded successfully!")
print(f"Total rows: {len(df)}")
df.head()

Data loaded successfully!
Total rows: 20499


ocel:eid       ocel:activity  \
13018  e-ha_a316c4d3a45247b7_2018-02-16 09:00:00  Hospital Admission   
13019                      e-bs_f614ff9287781917        Book Surgery   
13020                      e-bs_f614ff9287781917        Book Surgery   
13021                      e-bs_f614ff9287781917        Book Surgery   
13022                      e-in_f614ff9287781917             Room IN   

                 ocel:timestamp                   ocel:oid ocel:type  \
13018 2018-02-16 09:00:00+00:00         p_a316c4d3a45247b7   patient   
13019 2018-02-16 09:01:00+00:00         p_a316c4d3a45247b7   patient   
13020 2018-02-16 09:01:00+00:00  r_Severe Systemic Disease    rating   
13021 2018-02-16 09:01:00+00:00         s_f614ff9287781917   surgery   
13022 2018-02-16 11:32:00+00:00         s_f614ff9287781917   surgery   

      ocel:qualifier  
13018           None  
13019           None  
13020           None  
13021           None  
13022           None

## Prepare data for analysis

In [3]:
# Create patient-centric view
patient_events = df[df['ocel:type'] == 'patient'].copy()
patient_events = patient_events.sort_values(['ocel:oid', 'ocel:timestamp'])

In [4]:
variants = pm4py.get_variants(patient_events, activity_key='ocel:activity', case_id_key='ocel:oid', timestamp_key='ocel:timestamp')

### All Transitions

In [5]:
all_variants = sorted(variants.items(), key=lambda x: (x[1], x[0]), reverse=True)
all_frequencies = [variant[1] for variant in all_variants]
all_percentages = [(freq / sum(all_frequencies)) * 100 for freq in all_frequencies]
all_variant_names = [variant[0] for variant in all_variants]
transition_names = [' -> '.join(variant) for variant in all_variant_names]
transition_df = pd.DataFrame({
    'Frequency': all_frequencies,
    'Precentage': all_percentages,
    'Transition': transition_names
})
transition_df

Frequency  Precentage                                         Transition
0         527   47.179946  Hospital Admission -> Book Surgery -> Room IN ...
1         326   29.185318  Hospital Admission -> Book Surgery -> Room IN ...
2          63    5.640107  Hospital Admission -> Book Surgery -> Room IN ...
3          50    4.476276  Hospital Admission -> Book Surgery -> Anesthes...
4          31    2.775291  Hospital Admission -> Book Surgery -> Anesthes...
5          23    2.059087  Hospital Admission -> Book Surgery -> Cancel S...
6          19    1.700985  Hospital Admission -> Book Surgery -> Cancel S...
7          16    1.432408  Hospital Admission -> Book Surgery -> Room IN ...
8          10    0.895255  Hospital Admission -> Book Surgery -> Cancel S...
9           6    0.537153  Hospital Admission -> Book Surgery -> Anesthes...
10          5    0.447628  Hospital Admission -> Book Surgery -> Room IN ...
11          5    0.447628  Hospital Admission -> Book Surgery -> Room IN ...
12          4    0.358102  Hospital Admission -> Book Surgery -> Room IN ...
13          4    0.358102  Hospital Admission -> Book Surgery -> Cancel S...
14          3    0.268577  Hospital Admission -> Book Surgery -> Room IN ...
15          3    0.268577  Hospital Admission -> Book Surgery -> Room IN ...
16          3    0.268577  Hospital Admission -> Book Surgery -> Cancel S...
17          3    0.268577  Hospital Admission -> Book Surgery -> Cancel S...
18          2    0.179051  Hospital Admission -> Book Surgery -> Room IN ...
19          2    0.179051  Hospital Admission -> Book Surgery -> Cancel S...
20          2    0.179051  Hospital Admission -> Book Surgery -> Anesthes...
21          1    0.089526  Hospital Admission -> Book Surgery -> Room IN ...
22          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
23          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
24          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
25          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
26          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
27          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
28          1    0.089526  Hospital Admission -> Book Surgery -> Cancel S...
29          1    0.089526  Hospital Admission -> Book Surgery -> Anesthes...
30          1    0.089526  Hospital Admission -> Book Surgery -> Anesthes...

### Top 10 Variants

In [6]:
variants_count = sorted(variants.items(), key=lambda x: (x[1], x[0]), reverse=False)
top_variants = variants_count[-10:]
variant_names = [variant[0] for variant in top_variants]
frequencies = [variant[1] for variant in top_variants]
percentages = [(freq / sum(frequencies)) * 100 for freq in frequencies]

In [7]:
# Color scheme for different activity types
activity_colors = {
    'Hospital Admission': '#D7E3FF',
    'Book Surgery': '#EAB3AE',
    'Room IN': '#B2F0EA',
    'Room OUT': '#9BD5CF',
    'Anesthesia Start': '#E4D7FF',
    'Anesthesia Ready': '#EADFFF',
    'Anesthesia Stop': '#D5C2FF',
    'PACU_ICU': '#D6F5D6',
    'Cancel Surgery': '#FFC7C2',
    'Discharge': '#D7E3FF',
}

# Create DOT content as string
dot_content = '''digraph SurgicalProcessVariants {
    // Modern graph settings
    graph [
        rankdir=LR,
        splines=true,
        ranksep=0.5,
        nodesep=0.3,
        bgcolor="white",
        fontname="Arial",
        pad=0.0,
        dpi=600
    ];
    
    node [
        style="filled,rounded",
        width=1.2,
        height=0.6,
        shape=box,
        penwidth=1.5,
        margin=0.12,
        fontname="Arial"
    ];
    
    edge [
        fontname="Arial",
        fontsize=10,
        arrowsize=2,
        penwidth=5
    ];
'''
cluster_color = "#BDBDBD"
cluster_fill = "#F5F5F5"
label_color = "#000000"
freq_font_size = 16
activity_font_size = 14

# Add each variant as a subgraph cluster
for idx, (freq, percent, activities) in enumerate(zip(frequencies, percentages, variant_names)):
    dot_content += f'''
    // PATHWAY {idx} - Frequency: {freq} ({percent}%)
    subgraph cluster_{idx} {{
        label="";
        style="rounded,filled";
        fillcolor="{cluster_fill}";
        color="{cluster_color}";
        penwidth=2.5;
        fontname="Arial";
        margin=15;
        '''
    # Add frequency label as a separate node on the left
    dot_content += f'freq_{idx} [label="Freq: {freq}\\n({percent:.2f}%)", shape=folder, style="filled", fillcolor="#E0E0E0", fontcolor="#424242", fontsize={freq_font_size}, penwidth=1.5];\n'
    
    # Add nodes for this variant
    for i, activity in enumerate(activities):
        node_id = f'v{idx}_{i}'
        color = activity_colors.get(activity, '#E0E0E0')
        #label = activity.replace('Admission', '\\nAdmission').replace('Surgery', '\\nSurgery').replace('Start', '\\nStart').replace('Ready', '\\nReady').replace('Stop', '\\nStop').replace('IN', '\\nIN').replace('OUT', '\\nOUT')
        label = '\\n'.join([word for word in activity.split()])
        dot_content += f'        {node_id} [label="{label}", fillcolor="{color}", fontcolor="#212121", fontsize={activity_font_size}];\n'
    
    dot_content += f'        freq_{idx} -> v{idx}_0 [penwidth="0", arrowsize="0"];\n'
    
    # Add edges for this variant
    for i in range(len(activities) - 1):
        from_node = f'v{idx}_{i}'
        to_node = f'v{idx}_{i+1}'
        dot_content += f'        {from_node} -> {to_node} [color="{cluster_color}"];\n'
    
    dot_content += '    }\n'

dot_content += '}\n'

# Write DOT file
with open('templates/figure_4.dot', 'w', encoding='utf-8') as f:
    f.write(dot_content)

# Create graph from DOT content
graph = pydot.graph_from_dot_data(dot_content)[0]

# Save as PNG
graph.write_png('results/figure_4.png')

In [8]:
from IPython.display import Image
Image("results/figure_4.png")

### Figure 5

In [9]:
graph = pydot.graph_from_dot_file("templates/figure_5.dot")[0]
graph.write_png("results/figure_5.png")

import subprocess
subprocess.run([
    "dot",
    "-Tpng",
    "-Gdpi=600",
    "templates/figure_5.dot",
    "-o",
    "results/figure_5.png"
])

CompletedProcess(args=['dot', '-Tpng', '-Gdpi=600', 'templates/figure_5.dot', '-o', 'results/figure_5.png'], returncode=0)

In [10]:
from IPython.display import Image
Image("results/figure_5.png")